In [1]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point
%matplotlib inline
import seaborn as sns; sns.set_theme(color_codes=True)
pd.set_option('display.max_columns', None)
import matplotlib.pyplot as plt
import numpy as np
import matplotlib.colors
import warnings
warnings.filterwarnings('ignore')
import osmnx as ox

In [21]:
#north, south, east, west
#G = ox.graph_from_place("Oradell,NJ,USA", network_type='drive')
G=ox.graph_from_bbox(41.01132359438095, 40.90736914977194, -74.07244863958279, -73.97009723735901, network_type='drive')


In [72]:
nodes, edges = ox.utils_graph.graph_to_gdfs(G)
edges.head()

osmid              name      highway  oneway  \
u         v         key                                                    
103092996 103092998 0    11562242      Dulles Drive  residential   False   
          103155753 0    11569129  Sunnyside Avenue  residential   False   
          103281584 0    11589122  Shadyside Avenue  residential   False   
103092998 103269521 0    11584035      Depew Street  residential   False   
          103269519 0    11584035      Depew Street  residential   False   

                          length  \
u         v         key            
103092996 103092998 0    264.189   
          103155753 0    336.250   
          103281584 0    342.140   
103092998 103269521 0     74.477   
          103269519 0     75.116   

                                                                  geometry  \
u         v         key                                                      
103092996 103092998 0    LINESTRING (-73.99087 40.93710, -73.99051 40.9...   
          103155753 0    LINESTRING (-73.99087 40.93710, -73.99087 40.9...   
          103281584 0    LINESTRING (-73.99087 40.93710, -73.99089 40.9...   
103092998 103269521 0    LINESTRING (-73.98775 40.93730, -73.98780 40.9...   
          103269519 0    LINESTRING (-73.98775 40.93730, -73.98770 40.9...   

                         ref lanes maxspeed bridge junction access tunnel  
u         v         key                                                    
103092996 103092998 0    NaN   NaN      NaN    NaN      NaN    NaN    NaN  
          103155753 0    NaN   NaN      NaN    NaN      NaN    NaN    NaN  
          103281584 0    NaN   NaN      NaN    NaN      NaN    NaN    NaN  
103092998 103269521 0    NaN   NaN      NaN    NaN      NaN    NaN    NaN  
          103269519 0    NaN   NaN      NaN    NaN      NaN    NaN    NaN

In [73]:
streets = edges.explode('highway')

In [74]:
streets['highway'].unique() 

array(['residential', 'tertiary', 'primary', 'trunk_link',
       'motorway_link', 'secondary', 'secondary_link', 'trunk',
       'motorway', 'unclassified', 'living_street', 'primary_link',
       'tertiary_link'], dtype=object)

In [75]:
# select only highway, osmid and geometry
streets = streets[['highway', 'osmid', 'geometry']]

In [76]:
# reset index and explode osmid
streets = streets.explode('osmid').reset_index(drop=True)

In [77]:
streets

highway       osmid  \
0        residential    11562242   
1        residential    11569129   
2        residential    11589122   
3        residential    11584035   
4        residential    11584035   
...              ...         ...   
16891        primary  1124856232   
16892        primary  1124856235   
16893        primary  1124856232   
16894  motorway_link  1124856237   
16895  motorway_link  1124856238   

                                                geometry  
0      LINESTRING (-73.99087 40.93710, -73.99051 40.9...  
1      LINESTRING (-73.99087 40.93710, -73.99087 40.9...  
2      LINESTRING (-73.99087 40.93710, -73.99089 40.9...  
3      LINESTRING (-73.98775 40.93730, -73.98780 40.9...  
4      LINESTRING (-73.98775 40.93730, -73.98770 40.9...  
...                                                  ...  
16891  LINESTRING (-74.06738 40.96482, -74.06749 40.9...  
16892  LINESTRING (-74.06738 40.96482, -74.06749 40.9...  
16893  LINESTRING (-74.06671 40.96443, -74.06688 40.9...  
16894  LINESTRING (-74.06671 40.96443, -74.06683 40.9...  
16895  LINESTRING (-74.06671 40.96443, -74.06683 40.9...  

[16896 rows x 3 columns]

In [29]:
#save to shapefile
#streets.to_file('data/seattle-osm-roads/seattle-osm-roads.shp')

In [65]:
streets.explore(tiles='cartodbpositron', column='highway')

In [78]:
#read in geojson file for streets
ps_streets = gpd.read_file('data/source/streets.json')

In [79]:
ps_streets['osm_id'].nunique()

203

In [80]:

#drop avg_image_date and avg_label_date
ps_streets = ps_streets.drop(['avg_image_date', 'avg_label_date'], axis=1)

In [81]:
#select the ones in streets that are in ps_streets by osmid
streets = streets[streets['osmid'].isin(ps_streets['osm_id'])]

In [83]:
#grouby osmid and pick the first highway type
grouped = streets.groupby('osmid').first().reset_index()
#drop the geometry column
grouped = grouped.drop('geometry', axis=1)

In [84]:
grouped

osmid      highway
0      11562297  residential
1      11564127  residential
2      11564531  residential
3      11564801  residential
4      11564836  residential
..          ...          ...
198   918422008     tertiary
199   970939924    secondary
200   970939925    secondary
201  1014487602      primary
202  1027007129      primary

[203 rows x 2 columns]

In [85]:
#merge the two dataframes
df= ps_streets.merge(grouped, left_on='osm_id', right_on='osmid')

In [88]:
df = df.drop('osmid', axis=1)

In [92]:
df.explore(tiles='cartodbpositron', column='highway', cmap='Set2')

In [93]:
!mkdir data/ordell-osm-roads
df.to_file('data/ordell-osm-roads/ordell-osm-roads.shp')